In [1]:
import psi4

In [2]:
# Z-matrix with just one value at equilibrium distance
mol = """H
F 1 0.91"""

# Get mol as Psi4 molecule
molecule = psi4.geometry(mol)

# Calculate energy and get wavefunction.
# Added the argument return_wfn=True to energy function. 
# Now the function returns two values, the energy and the wavefunction
energy, wfn = psi4.energy("CCSD/cc-pVTZ", molecule=molecule, return_wfn=True)

In [3]:
help(psi4.cubeprop)

  -0.0185083871

    SCF energy       (wfn)                    = -100.058278764373981
    Reference energy (file100)                = -100.058278764373910

    Opposite-spin MP2 correlation energy      =   -0.211978813770943
    Same-spin MP2 correlation energy          =   -0.072660901723823
    Singles MP2 correlation energy            =   -0.000000000000000
    MP2 correlation energy                    =   -0.284639715494766
      * MP2 total energy                      = -100.342918479868672

    Opposite-spin CCSD correlation energy     =   -0.221236468283630
    Same-spin CCSD correlation energy         =   -0.065359282656058
    Singles CCSD correlation energy           =    0.000000000000000
    CCSD correlation energy                   =   -0.286595750939688
      * CCSD total energy                     = -100.344874515313592

Help on function cubeprop in module psi4.driver.p4util.util:

cubeprop(wfn, **kwargs)
    Evaluate properties on a grid and generate cube files.
    
  

In [3]:
# Set options for Psi4

HOMO = 8
LUMO = 9 # These are is the HOMO and LUMO for HF.
                # The HOMO/LUMO is based on the total number of electrons. HF has 10 electrons
                # and each orbital can have two electrons. 5 is the HOMO and 6 is the LUMO


psi4.set_options({
    'CUBEPROP_TASKS': ['ORBITALS'], # calculate orbitals
    'CUBEPROP_ORBITALS': [HOMO-1, HOMO, LUMO, LUMO+1],    # calculate HOMO and LUMO. 
})
cube = psi4.cubeprop(wfn)

In [4]:
ls

CQED_RHF.py                         example-cube.ipynb
CS_CQED_CIS.py                      geom.xyz
Formaldehyde.ipynb                  helper_cis.py
Formaldehyde_ccpVDZ_variable_L.txt  helper_cqed_rhf.py
LICENSE                             helper_cs_cqed_cis.py
Psi_a_5_1-B2.cube                   mgh_exploration.ipynb
Psi_a_6_4-A1.cube                   output.dat
README.md                           psi.61883.clean
__pycache__/                        timer.dat


In [5]:
# Save molecule as xyz file.
# This is a function that will create a file called "HF.xyz"
molecule.save_xyz_file("geom.xyz", 1)

In [6]:
# Read in the file we just wrote
# Read xyz into string (we have to do this for the visualization library)
f = open("geom.xyz")
xyz = f.read()
f.close()

In [7]:
# Import molecular visualization library
import py3Dmol

In [8]:
def open_cube(cube_file):
    """
    Open and parse a cube file.
    
    The low and high isovalues are returned, along with the cube values. The low and high values represent the
    isocontour range for 85% of the density.
    
    Parameters
    ----------
    cube_file : str
        The filepath to the cube file to read.
    
    Returns
    -------
    low : float
        Low limit for isocontour range to capture 85% of the density.
    high : float
        High limit for isocontour range to capture 85% of the density.
    
    """
    
    # Get isovalues
    f = open(cube_file, "r")
    f.readline()
    line = f.readline()
    f.close()
    split_line = line.split(":")
    
    isovalues = split_line[-1][2:-2]
    isovalues = isovalues.split(",")
    
    high = float(isovalues[1])
    low = float(isovalues[0])
    
    # Read cube file
    f = open(cube_file, "r")
    data = f.read()
    f.close()
    
    return low, high, data

In [9]:
import glob

In [10]:
# get all the cube files
cube_files = glob.glob("*.cube")

In [11]:
for cube in cube_files:
    # Use the open_cube function
    isohigh, isolow, orbital = open_cube(cube)
    
    # Process the file name to get the orbital
    orbital_num = cube.split("_")[2]
    
    print(F"Showing visualization for orbital {orbital_num}")
    
    # Use pymol3D to make visualization
    v = py3Dmol.view()
    
    # Add surfaces
    v.addVolumetricData(orbital, "cube", {'isoval': isohigh, 'color': "red", 'opacity': 0.95})
    v.addVolumetricData(orbital, "cube", {'isoval': isolow, 'color': "blue", 'opacity': 0.95})
    
    # Add molecule
    v.addModel(xyz, 'mol')
    v.setStyle({'stick':{}})
    
    # Zoom to molecule and show
    v.zoomTo()
    v.show()

Showing visualization for orbital 6


You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

Showing visualization for orbital 5


You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol